In [2]:
from __future__ import print_function
import os
import neat

import pandas as pd
import numpy as np
import random

import torch
import torch.nn as nn
import torch.optim as optim


from explaneat.core.backprop import NeatNet
from explaneat.core import backprop
from explaneat.core.backproppop import BackpropPopulation
# from explaneat.visualization import visualize
from explaneat.core.experiment import ExperimentReporter
from explaneat.core.utility import one_hot_encode


from sklearn import datasets
from sklearn import metrics
from sklearn.preprocessing import StandardScaler

from copy import deepcopy

import time
from datetime import datetime


import gzip
try:
    import cPickle as pickle  # pylint: disable=import-error
except ImportError:
    import pickle  # pylint: disable=import-error

In [3]:

USE_CUDA = torch.cuda.is_available()
# USE_CUDA = False
device = torch.device("cuda:1" if USE_CUDA else "cpu")


# Breast Cancer Experiment

This experiment (a) test the experimental environment, but is also to evaluate the efficacy of the ExplaNEAT algorithm. Speed is a critical factor, as well as stability of results on population size. Total run time will also be measured

First, we need to set a random seed and a total stopping point in the number of generations

In [4]:
my_random_seed = 42
random.seed(my_random_seed)

In [5]:
def one_hot_encode(vals):
    width = max(vals)
    newVals = []
    for val in vals:
        blank = [0. for _ in range(width + 1)]
        blank[val] = 1.
        newVals.append(blank)
    return np.asarray(newVals)


## Dataset

We are going to work with the Iris dataset, which will be loaded from `sklearn`. We want to characterise the efficacy of the algorithm with regards to a mostly untransformed dataset, so we will only normalise the features

In [6]:
breast_cancer = datasets.load_breast_cancer()
xs_raw = breast_cancer.data[:, :]
scaler = StandardScaler()
scaler.fit(xs_raw)
xs = scaler.transform(xs_raw)
ys = breast_cancer.target.astype(np.float32)
# ys_onehot = one_hot_encode(ys)

In [7]:
# xs = torch.from_numpy(xs).to(device)
# ys = torch.from_numpy(ys).to(device)
xs = xs.tolist()
ys = ys.tolist()

ys = [[y] for y in ys]

Let's have a look at the data we are working with

In [8]:
ys[18:23]

[[0.0], [1.0], [1.0], [1.0], [0.0]]

In [9]:
xs[18:20]

[[1.6139698184696574,
  0.6656229931455752,
  1.5665031298586416,
  1.7209974817362566,
  0.13875260043374565,
  -0.03109907795326128,
  0.7420073820219539,
  1.188092857454763,
  -0.8383246182705409,
  -1.254240761107136,
  1.2741519919823439,
  -0.3626028457435921,
  1.484567482377281,
  1.5855074617343239,
  -0.18233369604754976,
  -0.36597246391019567,
  0.0668539634191777,
  0.55376156214928,
  -0.8454062864569916,
  -0.680059550437724,
  2.28842973337852,
  0.8472399004250337,
  2.369129468150238,
  2.6674864068466255,
  0.8254914662523765,
  0.3863591773388819,
  1.2713989863534898,
  1.8910486371131627,
  -0.21476961656157492,
  -0.43201158422697017],
 [-0.16679919141384392,
  -1.1471622983665986,
  -0.18572798829603052,
  -0.25195650134683506,
  0.10174657061886144,
  -0.4368502521374081,
  -0.2782095697248652,
  -0.028609288968872486,
  0.26791123136298334,
  -0.7283096557696301,
  -0.4882252608116023,
  -0.7769989918796776,
  -0.40001405246133,
  -0.3691244226546321,
  0.473

## Performance metric

The NEAT implementation on which ExplaNEAT extends uses a single function call for evaluating fitness. Although this might be reworked for ExplaNEAT to be able to get consistency between the genome-evaluation and the backprop loss function, that can be reviewed later.

This use `Binary Cross Entropy Loss` from `PyTorch`

In [10]:
def eval_genomes(genomes, config):
    loss = nn.BCELoss()
    loss = loss.to(device)
    for genome_id, genome in genomes.items():
        net = neat.nn.FeedForwardNetwork.create(genome, config)
        preds = []
        for xi in xs:
            preds.append(net.activate(xi))
        genome.fitness = float(1./loss(torch.tensor(preds).to(device), torch.tensor(ys)))

## Base configuration

We are going to create the base configuration according to an external configuration file. Per experiment, we will adjust this, later, but this defines the defaults across all runs.

In [11]:
config_path = "./config-breast-cancer"
base_config = neat.Config(neat.DefaultGenome, neat.DefaultReproduction,
                     neat.DefaultSpeciesSet, neat.DefaultStagnation,
                     config_path)


In [12]:
base_config.pop_size

2

We also want to put a hard limit on how long this can go on for.

In [13]:
maxNGenerations = 20

We will create a method to manage the instantiation of a population on the basis of a specific config.

In [14]:
def instantiate_population(config, xs, ys, saveLocation):

    if not os.path.exists(saveLocation):
        os.makedirs(saveLocation)
        
    config.save(os.path.join(saveLocation, 'config.conf'))

    # Create the population, which is the top-level object for a NEAT run.
    p = BackpropPopulation(config, 
                            xs, 
                            ys, 
                            criterion=nn.BCELoss())

    # Add a stdout reporter to show progress in the terminal.
    p.add_reporter(neat.StdOutReporter(True))
    stats = neat.StatisticsReporter()
    p.add_reporter(stats)
    p.add_reporter(neat.Checkpointer(5, filename_prefix=str(saveLocation) + "checkpoint-" ))
    bpReporter = backprop.BackpropReporter(True)
    p.add_reporter(bpReporter)
    p.add_reporter(ExperimentReporter(saveLocation))
    
    return p

# Experiment 1: Vary population size

The first experiment is going to examine the difference in run time different population sizes. 

In [15]:
population_points = [2, 5, 10, 25, 50, 100]

In [16]:
base_config.pop_size

2

In [17]:
saveLocationTemplate = './../../data/experiments/breast-cancer/experiment-newpopulation-{}-{}/'

## Start the experiment

In [18]:
# xs.tolist()

In [19]:
ys[:5]

[[0.0], [0.0], [0.0], [0.0], [0.0]]

In [20]:
for pop_size in population_points:
    for iteration_no in range(5):
        my_random_seed += 1
        random.seed(my_random_seed)
        start_time = datetime.now()
        
        print("################################################")
        print("################################################")
        print("Starting population {} iteration {}".format(pop_size, iteration_no))
        print("Started at {}".format(start_time.strftime("%m/%d/%Y, %H:%M:%S")))
        print("################################################")
        print("################################################")
        
        
        config = deepcopy(base_config)
        config.pop_size = pop_size
        
        saveLocation = saveLocationTemplate.format(pop_size, iteration_no)
        
        p = instantiate_population(config, xs, ys, saveLocation)
        # Run for up to nGenerations generations.
        winner = p.run(eval_genomes, maxNGenerations)
        
        g = p.best_genome

        
        end_time = datetime.now()
        
        p.reporters.reporters[2].save_checkpoint(p.config, p.population, p.species, str(p.generation) + "-final")  
        
        winner_net = neat.nn.FeedForwardNetwork.create(winner, config)

        results = []
        for xi, xo in zip(xs, ys):
            output = winner_net.activate(xi)
            results.append([xi, xo, output])

        df = pd.DataFrame(results)
        df.to_csv(os.path.join(saveLocation, 'results.csv'))
        
        ancestry = p.reporters.reporters[3].trace_ancestry_of_species(g.key, p.reproduction.ancestors) 

        ancestors = {
            k: v['genome'] for k, v in p.reporters.reporters[3].ancestry.items()
        }
    
        
        ## Save all of these to disc
        filename = 'fullStatus.xplnt'
        print("Saving checkpoint to {0}".format(filename))

        with gzip.open(os.path.join(saveLocation, filename), 'w', compresslevel=5) as f:
            data = (p, g, ancestry, ancestors, random.getstate())
            pickle.dump(data, f, protocol=pickle.HIGHEST_PROTOCOL)
#         visualize.create_ancestry_video(p.config, 
#                                         g, 
#                                         ancestry, 
#                                         ancestors, 
#                                         p.reporters.reporters[1], 
#                                         pathname=saveLocation)
        print("################################################")
        print("################################################")
        print("Have finished population {} iteration {}".format(pop_size, iteration_no))
        print("Started at {}".format(start_time.strftime("%m/%d/%Y, %H:%M:%S")))
        print("The time is {}".format(end_time.strftime("%m/%d/%Y, %H:%M:%S")))
        print("################################################")
        print("################################################")
    

################################################
################################################
Starting population 2 iteration 0
Started at 03/09/2022, 15:12:24
################################################
################################################
The function - generationStart - has just started at 1646791944.161283

 ****** Running generation 0 ****** 

The function - generationStart - took 0.00015115737915039062 seconds to complete
The function - pre_backprop - has just started at 1646791944.161451
The function - pre_backprop - took 2.6702880859375e-05 seconds to complete
The function - backprop - has just started at 1646791944.161494
about to start backprop with 100 epochs
mean improvement: -0.2688314118997963
best improvement: -0.27530534388926214
best loss: 0.2058960939506191
The function - backprop - took 0.09153103828430176 seconds to complete
The function - post_backprop - has just started at 1646791944.253044
The function - post_backprop - took 2.09808349609375e

In [20]:
for indiv in iter(p.population):
    print(indiv)

1
2


In [ ]:
for a, b, in p.population.items():
    print(a, b)
    

In [ ]:
p